# Case Study: Energy Consumption Analysis 
## Team 3:

Cristopher Marcial Ortiz Hernandez <br>
José Raul Rodriguez Cantú <br>
Eddye León Jarquín Mayorga <br>
Daniel Martinez Valdés <br>
Teresa Carrillo

In [ ]:
# Installing prophet
!pip install pystan
!pip install prophet

In [ ]:
#Add all libraries on top to see which models do you use.
import pandas as pd
import numpy as np
import plotly.express as px
from pandas_profiling import ProfileReport
import scipy.stats as stats
import statsmodels.tsa.holtwinters as holt
from sklearn.metrics import mean_squared_error, mean_absolute_percentage_error
from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly
from sklearn.neural_network import MLPRegressor
from sklearn.datasets import make_regression
from sklearn.model_selection import train_test_split
from keras.models import Sequential
from keras.layers import Dense
import warnings
warnings.filterwarnings('ignore')

# Exploratory Data Analysis

In [ ]:
df = pd.read_excel('energy_data.xlsx')

In [ ]:
# We decided to remove 2 extra days so the years were of 365 days.
df = df[:-48]

In [ ]:
df.head()

Hour  energy_consumpt_2001  energy_consumpt_2002  full_temp_2001  \
0     1            631.623161            835.021567       -0.400000   
1     2            534.397104            711.875374       -0.733333   
2     3            453.538784            592.673215       -1.066667   
3     4            400.699718            526.997961       -1.400000   
4     5            378.171092            497.588642       -1.666667   

   full_humid_2001  full_temp_2002  full_humid_2002  
0        64.000000        7.600000        82.000000  
1        65.333333        7.733333        78.666667  
2        66.666667        7.866667        75.333333  
3        68.000000        8.000000        72.000000  
4        60.333333        8.333333        69.666667

### Data transformation for easier handling

In [ ]:
energy_df = pd.melt(df,
    id_vars = 'Hour', 
    value_vars = ['energy_consumpt_2001','energy_consumpt_2002'], 
    var_name = 'year', 
    value_name = 'energy_consumpt').replace({'energy_consumpt_2001':'2001', 'energy_consumpt_2002': '2002'}).sort_values(by=['Hour','year'])

In [ ]:
temp_df = pd.melt(df,
    id_vars = 'Hour', 
    value_vars = ['full_temp_2001','full_temp_2002'], 
    var_name = 'year', 
    value_name = 'full_temp').replace({'full_temp_2001':'2001', 'full_temp_2002': '2002'}).sort_values(by=['Hour','year'])

In [ ]:
humid_df = pd.melt(df,
    id_vars = 'Hour', 
    value_vars = ['full_humid_2001','full_humid_2002'], 
    var_name = 'year', 
    value_name = 'full_humid').replace({'full_humid_2001':'2001', 'full_humid_2002': '2002'}).sort_values(by=['Hour','year'])

In [ ]:
df = energy_df.merge(temp_df, on = ['Hour','year']).merge(humid_df, on = ['Hour','year'])
df = df.sort_values(by=['year','Hour']).reset_index(drop = True)
df['year'] = pd.to_numeric(df['year'])
#Result DataFrame by joining the year columns
df.head()

Hour  year  energy_consumpt  full_temp  full_humid
0     1  2001       631.623161  -0.400000   64.000000
1     2  2001       534.397104  -0.733333   65.333333
2     3  2001       453.538784  -1.066667   66.666667
3     4  2001       400.699718  -1.400000   68.000000
4     5  2001       378.171092  -1.666667   60.333333

In [ ]:
#Generates general report for easier exploratory analysis
#profile = ProfileReport(df, title="Energy Data Report")
#profile.to_file("energy.html")
#profile.to_notebook_iframe()

### Data cleaning

In [ ]:
df.describe()

Hour          year  energy_consumpt     full_temp    full_humid
count  17472.000000  17472.000000     17438.000000  17472.000000  17472.000000
mean    4368.500000   2001.500000       626.915710     17.960246     61.845696
std     2521.938131      0.500014       248.669017      7.835988     18.971401
min        1.000000   2001.000000     -1332.918388     -2.600000      3.000000
25%     2184.750000   2001.000000       472.249750     12.000000     47.000000
50%     4368.500000   2001.500000       574.171410     18.000000     64.666667
75%     6552.250000   2002.000000       793.579796     24.000000     77.333333
max     8736.000000   2002.000000      9896.924643     41.000000    100.000000

### Fill NaN

In [ ]:
# NaNs of 2001 will be filled using interpolation as they're in between more values
df[df.year == 2001][df.isnull().any(axis=1)].head()

Hour  year  energy_consumpt  full_temp  full_humid
87     88  2001              NaN  10.000000   88.000000
144   145  2001              NaN  11.400000   64.000000
197   198  2001              NaN  11.266667   72.666667
212   213  2001              NaN  14.400000   70.666667
244   245  2001              NaN  11.733333   83.000000

In [ ]:
df['energy_consumpt'] = df.energy_consumpt.interpolate()

### Normalize extreme values

In [ ]:
# You can click on each variable in the legend to see only that column.
px.line(df, 
        x = 'Hour', 
        y = ['energy_consumpt','full_temp','full_humid'],
       title = 'Extreme values in data')

In [ ]:
#We created boxplots to visualize the outliers per variable.
fig = px.box(df[['energy_consumpt','full_temp','full_humid']].melt(),
       facet_col='variable',
       title = 'Energy Consumption, Temperature and Humidity Boxplots', 
       color = 'variable',
       color_discrete_sequence = ['palevioletred','lightseagreen','orange']).update_yaxes(matches=None)
for i in range(3):
    yaxis_name = 'yaxis' if i == 0 else f'yaxis{i + 1}'
    fig.layout[yaxis_name].showticklabels = True
fig.show()

#### As shown in the previous graphs, the column energy consumption has outliers, so we need to normalize them

In [ ]:
#Change values above upper fence of the box_plor which is 1275, negative values and zeros to NaNs and then interpolate
df.loc[df.energy_consumpt <= 0, 'energy_consumpt'] = np.nan
df.loc[df['energy_consumpt'] > 1276, 'energy_consumpt'] = np.nan
df['energy_consumpt'] = df.energy_consumpt.interpolate()

#### Now if we plot the data it should be more consistent

In [ ]:
# You can click on each variable in the legend to see only that column.
px.line(df[df.year==2002], 
        x = 'Hour', 
        y = ['energy_consumpt','full_temp','full_humid'],
       title = 'Extreme values in data')

In [ ]:
fig = px.box(df[['energy_consumpt','full_temp','full_humid']].melt(),
       facet_col='variable',
       title = 'Energy Consumption, Temperature and Humidity Boxplots', 
       color = 'variable',
       color_discrete_sequence = ['palevioletred','lightseagreen','orange']).update_yaxes(matches=None)
for i in range(3):
    yaxis_name = 'yaxis' if i == 0 else f'yaxis{i + 1}'
    fig.layout[yaxis_name].showticklabels = True
fig.show()

### Get the aggregated DataFrames (Hourly, daily, weekly)

In [ ]:
daily_df = df.groupby(df.index // 24).mean().reset_index().drop(columns='Hour').rename({'index':'day'}, axis = 1)
daily_df.head()

day    year  energy_consumpt  full_temp  full_humid
0    0  2001.0       609.008607   3.133333   42.666667
1    1  2001.0       586.616228   7.404167   61.791667
2    2  2001.0       594.213777   9.491667   85.125000
3    3  2001.0       612.099398   9.608333   83.916667
4    4  2001.0       592.807758  11.695833   82.125000

In [ ]:
weekly_df = df.groupby(df.index // 24 // 7).mean().reset_index().drop(columns='Hour').rename({'index':'week'}, axis = 1)
weekly_df.head()

week    year  energy_consumpt  full_temp  full_humid
0     0  2001.0       594.031576   9.121429   72.928571
1     1  2001.0       546.041233  11.944048   68.208333
2     2  2001.0       608.338953   4.657143   62.470238
3     3  2001.0       606.658393   6.276190   62.089286
4     4  2001.0       533.342763  12.290476   71.464286

### Correlation matrixes

In [ ]:
px.imshow(df.corr(), 
          text_auto = True, 
          color_continuous_scale='Greens',
          title = 'Correlation matrix of Hourly Energy Consumption')

In [ ]:
px.imshow(daily_df.corr(), 
          text_auto = True, 
          color_continuous_scale='Blues',
          title = 'Correlation matrix of Daily Energy Consumption')

In [ ]:
px.imshow(weekly_df.corr(), 
          text_auto = True, 
          color_continuous_scale='Reds',
          title = 'Correlation matrix of Weekly Energy Consumption')

As shown in the previous correlation matrixes, the energy consumption is highly correlated with the year. <br>
Which means that there was more energy consumption in 2002 than in 2001.

### Add a Date variable 

In [ ]:
df['Date'] = pd.to_datetime(int('271752') + df.Hour, unit='h')
daily_df['Date'] = pd.to_datetime(int('11323') + daily_df.day, unit='d')
weekly_df['Date'] = pd.to_datetime(1617.57143 + weekly_df.week, unit='W').dt.date

## Obtain prediction models for each frequency of observation. 
Compare different models (between the same frequency) and clearly state your final decision of the "best" model which can be used for prediction of energy load.

### First Method: Holt Winter's Exponential Smoothing with seasonal trend
For hourly data

In [ ]:
df = df.reset_index().drop(columns='Hour').rename({'index':'Hour'}, axis = 1)
X_train = df[:int(len(df)*.7)]
X_test = df[int(len(df)*.7):]

In [ ]:
%%time
model = holt.ExponentialSmoothing(X_train['energy_consumpt'], 
                                  trend = 'add',
                                  seasonal = 'add', 
                                  seasonal_periods = 24).fit(smoothing_seasonal = .45)
df['predict'] = model.predict(start = 1, end = len(df))

CPU times: user 660 ms, sys: 102 ms, total: 762 ms
Wall time: 659 ms


In [ ]:
px.line(df[-1000:],x='Hour', y = ['energy_consumpt', 'predict'])

In [ ]:
print('MSE:',mean_squared_error(df['energy_consumpt'][-len(X_test):], df['predict'][-len(X_test):]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(df['energy_consumpt'][-len(X_test):], df['predict'][-len(X_test):]) * 100))

MSE: 11874.329593565097
MAPE: 10.32 %


### First Method: Holt Winter's Exponential Smoothing with seasonal trend
For daily data

In [ ]:
X_train = daily_df[:int(len(daily_df)*.7)]
X_test = daily_df[int(len(daily_df)*.7):]

In [ ]:
%%time
model = holt.ExponentialSmoothing(X_train['energy_consumpt'], 
                                  trend = 'add',
                                  seasonal = 'mul', 
                                  seasonal_periods = 115).fit(smoothing_seasonal = .41)
daily_df['predict'] = model.predict(start = 1, end = len(daily_df))

CPU times: user 108 ms, sys: 3.51 ms, total: 111 ms
Wall time: 111 ms


In [ ]:
px.line(daily_df, x='day', y = ['energy_consumpt', 'predict'])

In [ ]:
print('MSE:',mean_squared_error(daily_df['energy_consumpt'][-len(X_test):], 
                                daily_df['predict'][-len(X_test):]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(daily_df['energy_consumpt'][-len(X_test):], 
                                                                      daily_df['predict'][-len(X_test):]) * 100))

MSE: 10597.224471012913
MAPE: 10.56 %


### First Method: Holt Winter's Exponential Smoothing with seasonal trend
For weekly data

In [ ]:
X_train = weekly_df[:int(len(weekly_df)*.7)]
X_test = weekly_df[int(len(weekly_df)*.7):]

In [ ]:
%%time
model = holt.ExponentialSmoothing(X_train['energy_consumpt'], 
                                  trend = 'add',
                                  seasonal = 'add', 
                                  seasonal_periods = 25).fit(smoothing_seasonal = .43)
weekly_df['predict'] = model.predict(start = 1, end = len(weekly_df))

CPU times: user 38 ms, sys: 2.6 ms, total: 40.6 ms
Wall time: 41.8 ms


In [ ]:
px.line(weekly_df, x='week', y = ['energy_consumpt', 'predict'])

In [ ]:
print('MSE:',mean_squared_error(weekly_df['energy_consumpt'][-len(X_test):], 
                                weekly_df['predict'][-len(X_test):]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(weekly_df['energy_consumpt'][-len(X_test):], 
                                                             weekly_df['predict'][-len(X_test):]) * 100))

MSE: 11353.031801672954
MAPE: 11.85 %


In [ ]:
#Store in separate csv
df.drop('predict',axis=1).to_csv('clean_hourly.csv', index=False)
daily_df.drop('predict',axis=1).to_csv('clean_daily.csv', index=False)
weekly_df.drop('predict',axis=1).to_csv('clean_weekly.csv', index=False)

## Second Method: Prophet
For daily data

In [ ]:
df_prophet = daily_df.copy()
df_prophet = df_prophet.drop(columns=['full_temp','full_humid','predict','year','Date'])
df_prophet['day'] = pd.to_datetime(df_prophet['day'], unit='D', origin=pd.Timestamp('2001'))
df_prophet = df_prophet.rename(columns={'day':'ds','energy_consumpt':'y'})
df_prophet.set_index('ds')
df_prophet.shape
df_prophet

ds           y
0   2001-01-01  609.008607
1   2001-01-02  586.616228
2   2001-01-03  594.213777
3   2001-01-04  612.099398
4   2001-01-05  592.807758
..         ...         ...
723 2002-12-25  872.631296
724 2002-12-26  872.631296
725 2002-12-27  936.969523
726 2002-12-28  947.213605
727 2002-12-29  965.400298

[728 rows x 2 columns]

In [ ]:
m = Prophet(interval_width=0.95, daily_seasonality=True)
model = m.fit(df_prophet)

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


### Make energy consumption prediction for the next 100 days


In [ ]:
future = m.make_future_dataframe(periods=100)
forecast = m.predict(future)
forecast.tail()

ds       trend  yhat_lower  yhat_upper  trend_lower  trend_upper  \
823 2003-04-04  781.768792  573.471534  918.330757   642.102535   905.136180   
824 2003-04-05  781.847191  577.728912  937.218448   639.573480   907.690683   
825 2003-04-06  781.925590  576.357210  933.300506   637.967928   910.039227   
826 2003-04-07  782.003989  574.360203  938.612788   636.362376   912.387761   
827 2003-04-08  782.082388  576.508682  948.053154   634.768399   914.698298   

     additive_terms  additive_terms_lower  additive_terms_upper     daily  \
823      -22.770410            -22.770410            -22.770410 -23.44921   
824      -29.059163            -29.059163            -29.059163 -23.44921   
825      -22.083316            -22.083316            -22.083316 -23.44921   
826      -23.796971            -23.796971            -23.796971 -23.44921   
827      -19.916699            -19.916699            -19.916699 -23.44921   

     daily_lower  daily_upper    weekly  weekly_lower  weekly_upper  \
823    -23.44921    -23.44921  0.678800      0.678800      0.678800   
824    -23.44921    -23.44921 -5.609953     -5.609953     -5.609953   
825    -23.44921    -23.44921  1.365895      1.365895      1.365895   
826    -23.44921    -23.44921 -0.347760     -0.347760     -0.347760   
827    -23.44921    -23.44921  3.532512      3.532512      3.532512   

     multiplicative_terms  multiplicative_terms_lower  \
823                   0.0                         0.0   
824                   0.0                         0.0   
825                   0.0                         0.0   
826                   0.0                         0.0   
827                   0.0                         0.0   

     multiplicative_terms_upper        yhat  
823                         0.0  758.998381  
824                         0.0  752.788028  
825                         0.0  759.842274  
826                         0.0  758.207018  
827                         0.0  762.165689

In [ ]:
df_prophet['yhat'] = forecast['yhat']
px.line(df_prophet, x='ds', y = ['y', 'yhat'])

In [ ]:
print('MSE:',mean_squared_error(df_prophet['y'][74:], df_prophet['yhat'][74:]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(df_prophet['y'][74:], df_prophet['yhat'][74:]) * 100))

MSE: 3909.3575486620184
MAPE: 7.22 %


## Third Method: Multilayer perceptron model
For hourly data

In [ ]:
models_df = df.drop(['year','full_temp','full_humid','predict','Date'], axis = 1)

In [ ]:
X_train = models_df[:int(len(df)*.7)]
X_test = models_df[int(len(df)*.7):]
y_train = models_df[:int(len(df)*.7)]['energy_consumpt']
y_test = models_df[int(len(df)*.7):]['energy_consumpt']

In [ ]:
%%time
regr = MLPRegressor(random_state=1, max_iter=500).fit(X_train, y_train)
predictions = regr.predict(X_test)

CPU times: user 2.57 s, sys: 2.83 s, total: 5.4 s
Wall time: 5.18 s


In [ ]:
energytrain = list(y_train)+(list(y_test))
vacio = np.empty(int(len(models_df)*.7))
vacio[:] = np.NaN
energyprediction = list(vacio)+list(predictions)
MLP_Hour_df = pd.DataFrame()
MLP_Hour_df['Hour'] = df['Hour']
MLP_Hour_df['energy_consumpt']=energytrain
MLP_Hour_df['predict'] = energyprediction

px.line(MLP_Hour_df, x='Hour', y = ['energy_consumpt', 'predict'])

In [ ]:
print('MSE:',mean_squared_error(MLP_Hour_df['energy_consumpt'][12302:], MLP_Hour_df['predict'][12302:]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(MLP_Hour_df['energy_consumpt'][12302:], MLP_Hour_df['predict'][12302:]) * 100))

MSE: 756.8117734471787
MAPE: 2.06 %


## Third Method: Multilayer perceptron model
For daily data

In [ ]:
models_df = daily_df.drop(['year','full_temp','full_humid','predict','Date'], axis = 1)

In [ ]:
X_train = models_df[:int(len(models_df)*.7)]
X_test = models_df[int(len(models_df)*.7):]
y_train = models_df[:int(len(models_df)*.7)]['energy_consumpt']
y_test = models_df[int(len(models_df)*.7):]['energy_consumpt']

In [ ]:
%%time
regr = MLPRegressor(random_state=1, max_iter=500).fit(X_train, y_train)
predictions = regr.predict(X_test)

CPU times: user 849 ms, sys: 681 ms, total: 1.53 s
Wall time: 799 ms


In [ ]:
vacio = np.empty(int(len(models_df)*.7))
vacio[:] = np.NaN
energytrain = list(y_train)+(list(y_test))
energyprediction = list(vacio)+list(predictions)
MLP_daily_df = pd.DataFrame()
MLP_daily_df['Day'] = daily_df['day']
MLP_daily_df['energy_consumpt']=energytrain
MLP_daily_df['predict'] = energyprediction

px.line(MLP_daily_df, x='Day', y = ['energy_consumpt', 'predict'])

In [ ]:
print('MSE:',mean_squared_error(MLP_daily_df['energy_consumpt'][513:], MLP_daily_df['predict'][513:]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(MLP_daily_df['energy_consumpt'][513:], MLP_daily_df['predict'][513:]) * 100))

MSE: 597.0324318905485
MAPE: 2.58 %


## Third Method: Multilayer perceptron model
For weekly data

In [ ]:
models_df = weekly_df.drop(['year','full_temp','full_humid','predict','Date'], axis = 1)

In [ ]:
X_train = models_df[:int(len(models_df)*.7)]
X_test = models_df[int(len(models_df)*.7):]
y_train = models_df[:int(len(models_df)*.7)]['energy_consumpt']
y_test = models_df[int(len(models_df)*.7):]['energy_consumpt']

In [ ]:
%%time
regr = MLPRegressor(random_state=1, max_iter=500).fit(X_train, y_train)
predictions = regr.predict(X_test)

CPU times: user 84.3 ms, sys: 0 ns, total: 84.3 ms
Wall time: 94.8 ms


In [ ]:
vacio = np.empty(int(len(models_df)*.7))
vacio[:] = np.NaN
energytrain = list(y_train)+(list(y_test))
energyprediction = list(vacio)+list(predictions)
MLP_weekly_df = pd.DataFrame()
MLP_weekly_df['week'] = weekly_df['week']
MLP_weekly_df['energy_consumpt']=energytrain
MLP_weekly_df['predict'] = energyprediction

px.line(MLP_weekly_df, x='week', y = ['energy_consumpt', 'predict'])

In [ ]:
print('MSE:',mean_squared_error(MLP_weekly_df['energy_consumpt'][74:], MLP_weekly_df['predict'][74:]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(MLP_weekly_df['energy_consumpt'][74:], MLP_weekly_df['predict'][74:]) * 100))

MSE: 810.2799000238327
MAPE: 3.79 %


## Fourth Method: Simple Moving Average
For hourly data

In [ ]:
models_df = df.drop(['year','full_temp','full_humid','predict','Date'], axis = 1)

In [ ]:
%%time
X_train = models_df[:int(len(models_df)*.7)]
X_test = models_df[int(len(models_df)*.7):]
y_train = models_df[:int(len(models_df)*.7)]['energy_consumpt']
y_test = models_df[int(len(models_df)*.7):]['energy_consumpt']

y_hat_sma = models_df.copy()
ma_window = 12
y_hat_sma['sma_forecast'] = models_df['energy_consumpt'].rolling(ma_window).mean()
y_hat_sma['sma_forecast'][len(X_train):] = y_hat_sma['sma_forecast'][len(X_train)-1]
y_hat_sma

px.line(y_hat_sma, x='Hour', y = ['energy_consumpt', 'sma_forecast'])

CPU times: user 494 ms, sys: 5.06 ms, total: 499 ms
Wall time: 727 ms


In [ ]:
print('MSE:',mean_squared_error(y_hat_sma['energy_consumpt'][12302:], y_hat_sma['sma_forecast'][12302:]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(y_hat_sma['energy_consumpt'][12302:], y_hat_sma['sma_forecast'][12302:]) * 100))

MSE: 38243.54736948962
MAPE: 23.14 %


## Fourth Method: Simple Moving Average
For daily data

In [ ]:
models_df = daily_df.drop(['year','full_temp','full_humid','predict','Date'], axis = 1)

In [ ]:
%%time
X_train = models_df[:int(len(models_df)*.7)]
X_test = models_df[int(len(models_df)*.7):]
y_train = models_df[:int(len(models_df)*.7)]['energy_consumpt']
y_test = models_df[int(len(models_df)*.7):]['energy_consumpt']

y_hat_sma = models_df.copy()
ma_window = 12
y_hat_sma['sma_forecast'] = models_df['energy_consumpt'].rolling(ma_window).mean()
y_hat_sma['sma_forecast'][len(X_train):] = y_hat_sma['sma_forecast'][len(X_train)-1]
y_hat_sma

px.line(y_hat_sma, x='day', y = ['energy_consumpt', 'sma_forecast'])

CPU times: user 94 ms, sys: 284 µs, total: 94.3 ms
Wall time: 106 ms


In [ ]:
print('MSE:',mean_squared_error(y_hat_sma['energy_consumpt'][513:], y_hat_sma['sma_forecast'][513:]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(y_hat_sma['energy_consumpt'][513:], y_hat_sma['sma_forecast'][513:]) * 100))

MSE: 9495.066004634982
MAPE: 9.63 %


## Fourth Method: Simple Moving Average
For weekly data

In [ ]:
models_df = weekly_df.drop(['year','full_temp','full_humid','predict','Date'], axis = 1)

In [ ]:
%%time
X_train = models_df[:int(len(models_df)*.7)]
X_test = models_df[int(len(models_df)*.7):]
y_train = models_df[:int(len(models_df)*.7)]['energy_consumpt']
y_test = models_df[int(len(models_df)*.7):]['energy_consumpt']

y_hat_sma = models_df.copy()
ma_window = 12
y_hat_sma['sma_forecast'] = models_df['energy_consumpt'].rolling(ma_window).mean()
y_hat_sma['sma_forecast'][len(X_train):] = y_hat_sma['sma_forecast'][len(X_train)-1]
models_df

px.line(y_hat_sma, x='week', y = ['energy_consumpt', 'sma_forecast'])

CPU times: user 86.4 ms, sys: 0 ns, total: 86.4 ms
Wall time: 114 ms


In [ ]:
print('MSE:',mean_squared_error(y_hat_sma['energy_consumpt'][74:], y_hat_sma['sma_forecast'][74:]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(y_hat_sma['energy_consumpt'][74:], y_hat_sma['sma_forecast'][74:]) * 100))

MSE: 4690.50842991713
MAPE: 7.95 %


### Fifth Method: Artificial Neural Network
For hourly data

In [ ]:
ANN_Hourly_df = df.drop(columns= ['predict','Date'])
ANN_Hourly_df

TargetVariable=['energy_consumpt']
Predictors=['Hour','year','full_temp', 'full_humid']

X = ANN_Hourly_df[Predictors].values
y = ANN_Hourly_df[TargetVariable].values

### Sandardization of data ###
from sklearn.preprocessing import StandardScaler
PredictorScaler=StandardScaler()
TargetVarScaler=StandardScaler()

# Storing the fit object for later reference
PredictorScalerFit=PredictorScaler.fit(X)
TargetVarScalerFit=TargetVarScaler.fit(y)

# Generating the standardized values of X and y
X=PredictorScalerFit.transform(X)
y=TargetVarScalerFit.transform(y)

# Split the data into training and testing set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, shuffle = False)

In [ ]:
# create ANN model
model = Sequential()
 
# Defining the Input layer and FIRST hidden layer, both are same!
model.add(Dense(units=5, input_dim=4, kernel_initializer='normal', activation='relu'))
 
# Defining the Second layer of the model
# after the first layer we don't have to specify input_dim as keras configure it automatically
model.add(Dense(units=5, kernel_initializer='normal', activation='tanh'))
 
# The output neuron is a single fully connected node 
# Since we will be predicting a single number
model.add(Dense(1, kernel_initializer='normal'))
 
# Compiling the model
model.compile(loss='mean_squared_error', optimizer='adam')
 
# Fitting the ANN to the Training set
model.fit(X_train, y_train ,batch_size = 20, epochs = 50, verbose=1)

Epoch 1/50
612/612 [==============================] - 3s 4ms/step - loss: 0.6033
Epoch 2/50
612/612 [==============================] - 2s 3ms/step - loss: 0.4791
Epoch 3/50
612/612 [==============================] - 2s 3ms/step - loss: 0.4703
Epoch 4/50
612/612 [==============================] - 1s 2ms/step - loss: 0.4652
Epoch 5/50
612/612 [==============================] - 2s 3ms/step - loss: 0.4637
Epoch 6/50
612/612 [==============================] - 2s 3ms/step - loss: 0.4616
Epoch 7/50
612/612 [==============================] - 1s 2ms/step - loss: 0.4573
Epoch 8/50
612/612 [==============================] - 1s 2ms/step - loss: 0.4536
Epoch 9/50
612/612 [==============================] - 1s 2ms/step - loss: 0.4509
Epoch 10/50
612/612 [==============================] - 1s 2ms/step - loss: 0.4471
Epoch 11/50
612/612 [==============================] - 2s 3ms/step - loss: 0.4434
Epoch 12/50
612/612 [==============================] - 2s 3ms/step - loss: 0.4393
Epoch 13/50
612/612 [====

In [ ]:
%%time
# Defining a function to find the best parameters for ANN
def FunctionFindBestParams(X_train, y_train, X_test, y_test):
    
    # Defining the list of hyper parameters to try
    batch_size_list=[5, 10, 15, 20]
    epoch_list  =   [5, 10, 25, 50]
    
    import pandas as pd
    SearchResultsData=pd.DataFrame(columns=['TrialNumber', 'Parameters', 'Accuracy'])
    
    # initializing the trials
    TrialNumber=0
    for batch_size_trial in batch_size_list:
        for epochs_trial in epoch_list:
            TrialNumber+=1
            # create ANN model
            model = Sequential()
            # Defining the first layer of the model
            model.add(Dense(units=5, input_dim=X_train.shape[1], kernel_initializer='normal', activation='relu'))
 
            # Defining the Second layer of the model
            model.add(Dense(units=5, kernel_initializer='normal', activation='relu'))
 
            # The output neuron is a single fully connected node 
            # Since we will be predicting a single number
            model.add(Dense(1, kernel_initializer='normal'))
 
            # Compiling the model
            model.compile(loss='mean_squared_error', optimizer='adam')
 
            # Fitting the ANN to the Training set
            model.fit(X_train, y_train ,batch_size = batch_size_trial, epochs = epochs_trial, verbose=0)
 
            MAPE = np.mean(100 * (np.abs(y_test-model.predict(X_test))/y_test))
            
            # printing the results of the current iteration
            print(TrialNumber, 'Parameters:','batch_size:', batch_size_trial,'-', 'epochs:',epochs_trial, 'Accuracy:', 100-MAPE)
            
            SearchResultsData=SearchResultsData.append(pd.DataFrame(data=[[TrialNumber, str(batch_size_trial)+'-'+str(epochs_trial), 100-MAPE]],
                                                                    columns=['TrialNumber', 'Parameters', 'Accuracy'] ))
    return(SearchResultsData)
 
 
######################################################
# Calling the function
ResultsData=FunctionFindBestParams(X_train, y_train, X_test, y_test)

1 Parameters: batch_size: 5 - epochs: 5 Accuracy: 63.587518457508395
2 Parameters: batch_size: 5 - epochs: 10 Accuracy: -10.253402926822915
3 Parameters: batch_size: 5 - epochs: 25 Accuracy: 59.734143626128336
4 Parameters: batch_size: 5 - epochs: 50 Accuracy: 19.35868102846385
5 Parameters: batch_size: 10 - epochs: 5 Accuracy: 81.53132019594578
6 Parameters: batch_size: 10 - epochs: 10 Accuracy: 5.51929696139689
7 Parameters: batch_size: 10 - epochs: 25 Accuracy: 52.46588490388566
8 Parameters: batch_size: 10 - epochs: 50 Accuracy: 53.00971529951079
9 Parameters: batch_size: 15 - epochs: 5 Accuracy: 85.80272320296488
10 Parameters: batch_size: 15 - epochs: 10 Accuracy: 64.36651068626699
11 Parameters: batch_size: 15 - epochs: 25 Accuracy: 7.65530391088933
12 Parameters: batch_size: 15 - epochs: 50 Accuracy: 61.15572828783297
13 Parameters: batch_size: 20 - epochs: 5 Accuracy: 78.52523086998727
14 Parameters: batch_size: 20 - epochs: 10 Accuracy: 55.33825273922073
15 Parameters: batch_

In [ ]:
# Fitting the ANN to the Training set
model.fit(X_train, y_train ,batch_size = 20, epochs = 5, verbose=0)

# Generating Predictions on testing data
Predictions=model.predict(X_test)

# Scaling the predicted Price data back to original price scale
Predictions=TargetVarScalerFit.inverse_transform(Predictions)

# Scaling the y_test Price data back to original price scale
y_test_orig=TargetVarScalerFit.inverse_transform(y_test)

# Scaling the test data back to original scale
Test_Data=PredictorScalerFit.inverse_transform(X_test)

TestingData=pd.DataFrame(data=Test_Data, columns=Predictors)
TestingData['energy_consumpt']=y_test_orig
TestingData['Predicted Consumpt']=Predictions
TestingData

Hour    year  full_temp  full_humid  energy_consumpt  \
0     12230.0  2002.0  30.333333   28.333333       705.961303   
1     12231.0  2002.0  30.000000   29.000000       716.454104   
2     12232.0  2002.0  28.800000   35.666667       735.547777   
3     12233.0  2002.0  27.600000   42.333333       764.677574   
4     12234.0  2002.0  26.400000   49.000000       823.803852   
...       ...     ...        ...         ...              ...   
5237  17467.0  2002.0   6.200000   69.333333      1256.509762   
5238  17468.0  2002.0   5.000000   74.666667      1242.622846   
5239  17469.0  2002.0   3.800000   80.000000      1175.808433   
5240  17470.0  2002.0   3.266667   84.000000      1020.322168   
5241  17471.0  2002.0   2.733333   88.000000       840.207041   

      Predicted Consumpt  
0             765.042969  
1             761.290466  
2             747.235962  
3             740.067810  
4             740.067810  
...                  ...  
5237          360.135986  
5238          325.862122  
5239          292.668091  
5240          269.385712  
5241          246.691452  

[5242 rows x 6 columns]

In [ ]:
hourly_plot_df = pd.DataFrame()
vacio = np.empty(int(len(X_train)))
vacio[:] = np.NaN
energyprediction = list(vacio)+list(TestingData['Predicted Consumpt'])
hourly_plot_df['energy_consumpt'] = list(df[:int(len(X_train))]['energy_consumpt']) + list(TestingData['energy_consumpt'])
hourly_plot_df['predictions'] = energyprediction
px.line(hourly_plot_df, y = ['energy_consumpt', 'predictions'])

In [ ]:
print('MSE:',mean_squared_error(hourly_plot_df['energy_consumpt'][int(len(X_train)):], hourly_plot_df['predictions'][int(len(X_train)):]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(hourly_plot_df['energy_consumpt'][int(len(X_train)):], hourly_plot_df['predictions'][int(len(X_train)):]) * 100))

MSE: 61673.28404521574
MAPE: 24.48 %


### Fifth Method: Artificial Neural Network
For daily data

In [ ]:
ANN_daily_df = daily_df.drop(columns= ['predict'])
ANN_daily_df

TargetVariable=['energy_consumpt']
Predictors=['day','year','full_temp', 'full_humid']

X = ANN_daily_df[Predictors].values
y = ANN_daily_df[TargetVariable].values

### Sandardization of data ###
from sklearn.preprocessing import StandardScaler
PredictorScaler=StandardScaler()
TargetVarScaler=StandardScaler()

# Storing the fit object for later reference
PredictorScalerFit=PredictorScaler.fit(X)
TargetVarScalerFit=TargetVarScaler.fit(y)

# Generating the standardized values of X and y
X=PredictorScalerFit.transform(X)
y=TargetVarScalerFit.transform(y)

# Split the data into training and testing set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, shuffle = False)

print(X_train.shape)
print(y_train.shape)
print(X_test.shape)
print(y_test.shape)

(509, 4)
(509, 1)
(219, 4)
(219, 1)


In [ ]:
# create ANN model
model = Sequential()
 
# Defining the Input layer and FIRST hidden layer, both are same!
model.add(Dense(units=5, input_dim=4, kernel_initializer='normal', activation='relu'))
 
# Defining the Second layer of the model
# after the first layer we don't have to specify input_dim as keras configure it automatically
model.add(Dense(units=5, kernel_initializer='normal', activation='tanh'))
 
# The output neuron is a single fully connected node 
# Since we will be predicting a single number
model.add(Dense(1, kernel_initializer='normal'))
 
# Compiling the model
model.compile(loss='mean_squared_error', optimizer='adam')
 
# Fitting the ANN to the Training set
model.fit(X_train, y_train ,batch_size = 20, epochs = 50, verbose=1)

Epoch 1/50
26/26 [==============================] - 0s 1ms/step - loss: 1.0946
Epoch 2/50
26/26 [==============================] - 0s 1ms/step - loss: 1.0640
Epoch 3/50
26/26 [==============================] - 0s 2ms/step - loss: 0.9999
Epoch 4/50
26/26 [==============================] - 0s 1ms/step - loss: 0.8727
Epoch 5/50
26/26 [==============================] - 0s 1ms/step - loss: 0.6747
Epoch 6/50
26/26 [==============================] - 0s 1ms/step - loss: 0.4497
Epoch 7/50
26/26 [==============================] - 0s 1ms/step - loss: 0.2682
Epoch 8/50
26/26 [==============================] - 0s 1ms/step - loss: 0.1733
Epoch 9/50
26/26 [==============================] - 0s 1ms/step - loss: 0.1355
Epoch 10/50
26/26 [==============================] - 0s 1ms/step - loss: 0.1234
Epoch 11/50
26/26 [==============================] - 0s 1ms/step - loss: 0.1164
Epoch 12/50
26/26 [==============================] - 0s 1ms/step - loss: 0.1113
Epoch 13/50
26/26 [==============================

In [ ]:
# Calling the function
ResultsData=FunctionFindBestParams(X_train, y_train, X_test, y_test)

1 Parameters: batch_size: 5 - epochs: 5 Accuracy: 160.68048723289385
2 Parameters: batch_size: 5 - epochs: 10 Accuracy: 87.85211141965169
3 Parameters: batch_size: 5 - epochs: 25 Accuracy: 56.95082399974881
4 Parameters: batch_size: 5 - epochs: 50 Accuracy: 75.18976040701605
5 Parameters: batch_size: 10 - epochs: 5 Accuracy: 107.93213152458002
6 Parameters: batch_size: 10 - epochs: 10 Accuracy: 161.66177843155623
7 Parameters: batch_size: 10 - epochs: 25 Accuracy: 110.04573904469034
8 Parameters: batch_size: 10 - epochs: 50 Accuracy: 66.88922751992598
9 Parameters: batch_size: 15 - epochs: 5 Accuracy: 76.71544040711942
10 Parameters: batch_size: 15 - epochs: 10 Accuracy: 146.46117088632843
11 Parameters: batch_size: 15 - epochs: 25 Accuracy: 70.01042616635485
12 Parameters: batch_size: 15 - epochs: 50 Accuracy: 68.45128403384642
13 Parameters: batch_size: 20 - epochs: 5 Accuracy: -2.769367788548635
14 Parameters: batch_size: 20 - epochs: 10 Accuracy: 121.3235176642514
15 Parameters: ba

In [ ]:
%%time
# Fitting the ANN to the Training set
model.fit(X_train, y_train ,batch_size = 5, epochs = 5, verbose=0)

# Generating Predictions on testing data
Predictions=model.predict(X_test)

# Scaling the predicted Price data back to original price scale
Predictions=TargetVarScalerFit.inverse_transform(Predictions)

# Scaling the y_test Price data back to original price scale
y_test_orig=TargetVarScalerFit.inverse_transform(y_test)

# Scaling the test data back to original scale
Test_Data=PredictorScalerFit.inverse_transform(X_test)

TestingData=pd.DataFrame(data=Test_Data, columns=Predictors)
TestingData['energy_consumpt']=y_test_orig
TestingData['Predicted Consumpt']=Predictions
TestingData

CPU times: user 725 ms, sys: 56.4 ms, total: 781 ms
Wall time: 635 ms


In [ ]:
daily_plot_df = pd.DataFrame()
vacio = np.empty(int(len(X_train)))
vacio[:] = np.NaN
energyprediction = list(vacio)+list(TestingData['Predicted Consumpt'])
daily_plot_df['energy_consumpt'] = list(daily_df[:int(len(X_train))]['energy_consumpt']) + list(TestingData['energy_consumpt'])
daily_plot_df['predictions'] = energyprediction
px.line(daily_plot_df, y = ['energy_consumpt', 'predictions'])

In [ ]:
print('MSE:',mean_squared_error(daily_plot_df['energy_consumpt'][int(len(X_train)):], daily_plot_df['predictions'][int(len(X_train)):]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(daily_plot_df['energy_consumpt'][int(len(X_train)):], daily_plot_df['predictions'][int(len(X_train)):]) * 100))

MSE: 10479.595116562685
MAPE: 11.24 %


### Fifth Method: Artificial Neural Network
For weekly data

In [ ]:
ANN_weekly_df = weekly_df.drop(columns= ['predict'])
ANN_weekly_df

TargetVariable=['energy_consumpt']
Predictors=['year','week','full_temp', 'full_humid']

X = ANN_weekly_df[Predictors].values
y = ANN_weekly_df[TargetVariable].values

### Sandardization of data ###
from sklearn.preprocessing import StandardScaler
PredictorScaler=StandardScaler()
TargetVarScaler=StandardScaler()

# Storing the fit object for later reference
PredictorScalerFit=PredictorScaler.fit(X)
TargetVarScalerFit=TargetVarScaler.fit(y)

# Generating the standardized values of X and y
X=PredictorScalerFit.transform(X)
y=TargetVarScalerFit.transform(y)

# Split the data into training and testing set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, shuffle = False)

print(X_train.shape)
print(y_train.shape)
print(X_test.shape)
print(y_test.shape)

(72, 4)
(72, 1)
(32, 4)
(32, 1)


In [ ]:
# create ANN model
model = Sequential()
 
# Defining the Input layer and FIRST hidden layer, both are same!
model.add(Dense(units=5, input_dim=4, kernel_initializer='normal', activation='relu'))
 
# Defining the Second layer of the model
# after the first layer we don't have to specify input_dim as keras configure it automatically
model.add(Dense(units=5, kernel_initializer='normal', activation='tanh'))
 
# The output neuron is a single fully connected node 
# Since we will be predicting a single number
model.add(Dense(1, kernel_initializer='normal'))
 
# Compiling the model
model.compile(loss='mean_squared_error', optimizer='adam')
 
# Fitting the ANN to the Training set
model.fit(X_train, y_train ,batch_size = 20, epochs = 50, verbose=1)

Epoch 1/50
4/4 [==============================] - 0s 3ms/step - loss: 1.1171
Epoch 2/50
4/4 [==============================] - 0s 3ms/step - loss: 1.1140
Epoch 3/50
4/4 [==============================] - 0s 3ms/step - loss: 1.1100
Epoch 4/50
4/4 [==============================] - 0s 3ms/step - loss: 1.1067
Epoch 5/50
4/4 [==============================] - 0s 4ms/step - loss: 1.1027
Epoch 6/50
4/4 [==============================] - 0s 3ms/step - loss: 1.0984
Epoch 7/50
4/4 [==============================] - 0s 4ms/step - loss: 1.0945
Epoch 8/50
4/4 [==============================] - 0s 4ms/step - loss: 1.0891
Epoch 9/50
4/4 [==============================] - 0s 3ms/step - loss: 1.0835
Epoch 10/50
4/4 [==============================] - 0s 5ms/step - loss: 1.0770
Epoch 11/50
4/4 [==============================] - 0s 3ms/step - loss: 1.0705
Epoch 12/50
4/4 [==============================] - 0s 3ms/step - loss: 1.0618
Epoch 13/50
4/4 [==============================] - 0s 4ms/step - loss: 1.

In [ ]:
# Calling the function
ResultsData=FunctionFindBestParams(X_train, y_train, X_test, y_test)

1 Parameters: batch_size: 5 - epochs: 5 Accuracy: -11.800120602000646
2 Parameters: batch_size: 5 - epochs: 10 Accuracy: -24.249449634820337


3 Parameters: batch_size: 5 - epochs: 25 Accuracy: 2.5872029254604456


4 Parameters: batch_size: 5 - epochs: 50 Accuracy: -24.558602220769345
5 Parameters: batch_size: 10 - epochs: 5 Accuracy: -5.982757010678526
6 Parameters: batch_size: 10 - epochs: 10 Accuracy: -12.780432294045
7 Parameters: batch_size: 10 - epochs: 25 Accuracy: 22.522765300191423
8 Parameters: batch_size: 10 - epochs: 50 Accuracy: -35.92944313096288
9 Parameters: batch_size: 15 - epochs: 5 Accuracy: -3.7343333553123017
10 Parameters: batch_size: 15 - epochs: 10 Accuracy: -5.6523839499662785
11 Parameters: batch_size: 15 - epochs: 25 Accuracy: 3.5565339609203335
12 Parameters: batch_size: 15 - epochs: 50 Accuracy: 2.6877275870439234
13 Parameters: batch_size: 20 - epochs: 5 Accuracy: -2.5973636076797106
14 Parameters: batch_size: 20 - epochs: 10 Accuracy: -6.973361646705541
15 Parameters: batch_size: 20 - epochs: 25 Accuracy: -19.903997487380053
16 Parameters: batch_size: 20 - epochs: 50 Accuracy: 21.464601941750985


In [ ]:
%%time
# Fitting the ANN to the Training set
model.fit(X_train, y_train ,batch_size = 20, epochs = 37, verbose=0)

# Generating Predictions on testing data
Predictions=model.predict(X_test)

# Scaling the predicted Price data back to original price scale
Predictions=TargetVarScalerFit.inverse_transform(Predictions)

# Scaling the y_test Price data back to original price scale
y_test_orig=TargetVarScalerFit.inverse_transform(y_test)

# Scaling the test data back to original scale
Test_Data=PredictorScalerFit.inverse_transform(X_test)

TestingData=pd.DataFrame(data=Test_Data, columns=Predictors)
TestingData['energy_consumpt']=y_test_orig
TestingData['Predicted Consumpt']=Predictions
TestingData

CPU times: user 313 ms, sys: 18.2 ms, total: 331 ms
Wall time: 280 ms


In [ ]:
weekly_plot_df = pd.DataFrame()
vacio = np.empty(int(len(X_train)))
vacio[:] = np.NaN
energyprediction = list(vacio)+list(TestingData['Predicted Consumpt'])
weekly_plot_df['energy_consumpt'] = list(weekly_df[:int(len(X_train))]['energy_consumpt']) + list(TestingData['energy_consumpt'])
weekly_plot_df['predictions'] = energyprediction
px.line(weekly_plot_df, y = ['energy_consumpt', 'predictions'])

In [ ]:
print('MSE:',mean_squared_error(weekly_plot_df['energy_consumpt'][int(len(X_train)):], weekly_plot_df['predictions'][int(len(X_train)):]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(weekly_plot_df['energy_consumpt'][int(len(X_train)):], weekly_plot_df['predictions'][int(len(X_train)):]) * 100))

MSE: 10839.48802569911
MAPE: 11.83 %


## Separate day and night consumption analysis

In [ ]:
#We used for daytime the 12 hour period with more energy consumption (between 9 am and 9pm)
daytime_df = df[(df.Date.dt.hour >= 9) & (df.Date.dt.hour < 21)]
daytime_df = daytime_df.reset_index(drop=True).reset_index().drop('Hour', axis = 1).rename(columns={'index':'Hour'})
nighttime_df = df[~df.isin(daytime_df)].dropna()

In [ ]:
#Correlation of variables stay the same
px.imshow(daytime_df.corr(), 
          text_auto = True, 
          color_continuous_scale='Oranges',
          title = 'Correlation matrix of Daytime Energy Consumption')

In [ ]:
#Correlation of variables stay the same
px.imshow(nighttime_df.corr(), 
          text_auto = True, 
          color_continuous_scale='Greys',
          title = 'Correlation matrix of Nighttime Energy Consumption')

In [ ]:
X_train = daytime_df[:int(len(daytime_df)*.7)]
X_test = daytime_df[int(len(daytime_df)*.7):]

In [ ]:
model = holt.ExponentialSmoothing(X_train['energy_consumpt'], 
                                  trend = 'add',
                                  seasonal = 'add', 
                                  seasonal_periods = 12).fit(smoothing_seasonal = .45)
daytime_df['predict'] = model.predict(start = 1, end = len(df))

In [ ]:
px.line(daytime_df[:500].sort_values(by='Hour'),x='Hour', y = ['energy_consumpt', 'predict'])

In [ ]:
print('MSE:',mean_squared_error(daytime_df['energy_consumpt'][-len(X_test):], daytime_df['predict'][-len(X_test):]))
print('MAPE: {:.2f} %'.format(mean_absolute_percentage_error(daytime_df['energy_consumpt'][-len(X_test):], daytime_df['predict'][-len(X_test):]) * 100))

MSE: 1135230.2631706987
MAPE: 108.31 %


### Dates

In [ ]:
pd.to_datetime(int('271752'), unit='h')

Timestamp('2001-01-01 00:00:00')

In [ ]:
pd.to_datetime(int('11323'), unit='d')

Timestamp('2001-01-01 00:00:00')

In [ ]:
pd.to_datetime(1617.57143, unit='W')

Timestamp('2001-01-01 00:00:00.864000')